In [1]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
import json
# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
#spacy for lemmatization
#import spacy
# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  
import matplotlib.pyplot as plt
from matplotlib import rc
from matplotlib import rcParams
%matplotlib inline
import nltk
#nltk.download('stopwords')
#nltk.download('punkt')
# lemmatization russian language
import pymorphy2
import pymystem3
from pymystem3 import Mystem
from nltk import word_tokenize
from nltk.corpus import stopwords
stopwordsrus = set(stopwords.words('russian'))


C:\ProgramData\Anaconda3\lib\site-packages\nltk\decorators.py:68: DeprecationWarning: `formatargspec` is deprecated since Python 3.5. Use `signature` and the `Signature` object directly
  regargs, varargs, varkwargs, defaults, formatvalue=lambda value: ""
C:\ProgramData\Anaconda3\lib\site-packages\nltk\lm\counter.py:15: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Sequence, defaultdict


# When to apply LDA topic modeling
- If you are working with a small number of documents (or even a single document) it may well be that simple frequency counts (or TF-IDF) are sufficient. <br>
- However, if you have hundreds of documents from an archive and you wish to understand something of what the archive contains without necessarily reading every document, then topic modeling might be a good approach.

# Theory: How LDA model works and what's behind it
In latent diriclet allocaton (LDA) model, each document is considered to be characterized by a set of topics that is following the Dirichlet distribution. 

In LDA probabilistic topic modeling:
- a collection of documents (texts) $D$ is given
- Each document $d$ from the collection is a sequence of words $W_{d} = (w_{1}, ..., w_{n_{d}})$ from dictionary $W$, where $n_{d}$ - length of document d. 
- Each document may be related to one or several themes
- order of documents in collection is not important
- order of words in documents is neglected, each document is considered as "bag of words"
- document collection is considered as set of pairs "document-word" $(d,w), d \in D, w \in W_{d}$
- each topic $t\in T$, where $T$ - set of topics, is described by Dirichlet-distribution $p(w|t)$ on the range of $w\in W$, in other words there are topic vectors: $\phi_{t} = (p(w|t):w \in W)$
- each document $d\in D$ is described by Dirichlet-distribution $p(t|d)$ on the range of $t\in T$, in other words there are document vectors: $\theta_{d} = (p(t|d):t \in T)$
<br>

Probability of a pair "document-word" to occure can be written as: $p(d,w)=\sum\limits_{t\in T}p(t)p(w|t)p(d|t)$

To build a topic model means to find matrices $\Phi = ||p(w|t)||$ and $\Theta = ||p(t|d)||$ given collection $D$.

In order to find a solution, we need to solve the optimization problem, i.e. to maximaze the function: 
$\sum\limits_{d\in D}\sum\limits_{w\in d}n_{dw}logp(w|d)\to\max\limits_{\Phi,\Theta}$, <br>
where $n_{dw}$ is frequency of word $w$ in document $d$.

# Example:
Let's say we have three texts:<br>
"Dogs like playing."<br>
"Cats like milk."<br>
"Cats and dogs like eating and playing. I love dogs. They are adorable." <br>

The results from LDA model could be the following:<br>
Text1: 100% Topic1 + 0% Topic2<br>
Text2: 100% Topic2 + 0% Topic1<br>
Text3: 70% Topic2 + 30% Topic1<br>

Where each topic represented by a set of words (from most to least relevant):<br>
Topic1: 30% dog, 30% playing, 20% like 10% adorable 10% love<br>
Topic2: 50% cat, 30% milk, 20% like<br>


# The goals:
My goal will be:
- to find optimal N of topics
- to find most frequent topics(e.g. first 20) and their sets of keywords for collection of documents

In [41]:
# We will be using publically available dataset: https://www.kaggle.com/yutkin/corpus-of-russian-news-articles-from-lenta
# The dataset containes articles and news from online newspaper   

rus_data = pd.read_csv('C:/Users/genya/Topic modelling/lenta-ru-news.csv')

C:\ProgramData\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3058: DtypeWarning: Columns (3) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [42]:
rus_data

url  \
0        https://lenta.ru/news/1914/09/16/hungarnn/   
1       https://lenta.ru/news/1914/09/16/lermontov/   
2       https://lenta.ru/news/1914/09/17/nesteroff/   
3        https://lenta.ru/news/1914/09/17/bulldogn/   
4            https://lenta.ru/news/1914/09/18/zver/   
...                                             ...   
800970      https://lenta.ru/news/2019/12/14/shnur/   
800971       https://lenta.ru/news/2019/12/14/dolg/   
800972  https://lenta.ru/news/2019/12/14/dark_euro/   
800973      https://lenta.ru/news/2019/12/14/meteo/   
800974      https://lenta.ru/news/2019/12/14/olimp/   

                                                    title  \
0       1914. Русские войска вступили в пределы Венгрии     
1       1914. Празднование столетия М.Ю. Лермонтова от...   
2                                1914. Das ist Nesteroff!   
3                         1914. Бульдог-гонец под Льежем    
4                1914. Под Люблином пойман швабский зверь   
...                                                   ...   
800970          Шнуров раскритиковал Гагарину на «Голосе»   
800971  В России предложили изменить правила взыскания...   
800972          В России назвали «черную дату» для Европы   
800973        Россиянам пообещали аномально теплую погоду   
800974  В конкурсе прогнозов на АПЛ разыграют 100 тыся...   

                                                     text       topic  \
0       Бои у Сопоцкина и Друскеник закончились отступ...  Библиотека   
1       Министерство народного просвещения, в виду про...  Библиотека   
2       Штабс-капитан П. Н. Нестеров на днях, увидев в...  Библиотека   
3       Фотограф-корреспондент Daily Mirror рассказыва...  Библиотека   
4       Лица, приехавшие в Варшаву из Люблина, передаю...  Библиотека   
...                                                   ...         ...   
800970  Певец Сергей Шнуров раскритиковал свою коллегу...         NaN   
800971  Министерство юстиции России предложило изменит...         NaN   
800972  Испытание США ранее запрещенной Договором о ли...         NaN   
800973  В ближайшие дни в европейской части России пог...         NaN   
800974  Ведущие футбольные чемпионаты ушли на зимние к...         NaN   

                     tags        date  
0          Первая мировая  1914/09/16  
1          Первая мировая  1914/09/16  
2          Первая мировая  1914/09/17  
3          Первая мировая  1914/09/17  
4          Первая мировая  1914/09/18  
...                   ...         ...  
800970         ТВ и радио  2019/12/14  
800971                Все  2019/12/14  
800972           Политика  2019/12/14  
800973           Общество  2019/12/14  
800974  Английский футбол  2019/12/14  

[800975 rows x 6 columns]

In [43]:
rus_data['topic'].unique()

array(['Библиотека', 'Россия', 'Мир', 'Экономика', 'Интернет и СМИ',
       'Спорт', 'Культура', 'Из жизни', 'Силовые структуры',
       'Наука и техника', 'Бывший СССР', nan, 'Дом', 'Сочи', 'ЧМ-2014',
       'Путешествия', 'Ценности', 'Легпром', 'Бизнес', 'МедНовости',
       'Оружие', '69-я параллель', 'Культпросвет ', 'Крым'], dtype=object)

In [44]:
# Let's shorten the dataset and exclude some of the topics: 
rusdata = rus_data['text'][(rus_data['topic']!='Библиотека')&(rus_data['topic']!='Бывший СССР')&(rus_data['topic']!='69-я параллель')].reset_index(drop=True)

In [5]:
rusdata

0         Как стало известно агентству Ассошиэйтед Пресс...
1         В зале игровых автоматов в третьем ярусе подзе...
2         Япония приняла решение разморозить кредиты Рос...
3         Британцы отмечают сегодня скорбную дату - втор...
4         В понедельник директор департамента внешних св...
                                ...                        
746235    Певец Сергей Шнуров раскритиковал свою коллегу...
746236    Министерство юстиции России предложило изменит...
746237    Испытание США ранее запрещенной Договором о ли...
746238    В ближайшие дни в европейской части России пог...
746239    Ведущие футбольные чемпионаты ушли на зимние к...
Name: text, Length: 746240, dtype: object

In [71]:
# Loading stopwords
stops1 = []
with open('C:/Users/genya/Topic modelling/RussianStopWords.txt', "r", encoding="utf-8", newline=None) as readfile:
     [stops1.append(line.rstrip()) for line in readfile]

stops2 = []
with open('C:/Users/genya/Topic modelling/stopwords.txt', "r", encoding="utf-8", newline=None) as readfile:
     [stops2.append(line.rstrip()) for line in readfile]
    


In [72]:
# Combining stopwords
stopw_all = stops1 + stops2 + list(stopwordsrus)
stopwordsru = list(dict.fromkeys(stopw_all))

In [73]:
# Tokenizing and removing stopwords
def process(text):
    return list(t.lower() for t in word_tokenize(text) if t.isalpha() and t.lower() not in stopwordsru)
    

In [74]:
data = [process(t) for t in rusdata[:20000]]


In [75]:
# Lemmatizer for russian language
morph = pymorphy2.MorphAnalyzer()
def lemmatizer(texts):
    return [[morph.parse(word)[0] for word in text] for text in texts]

In [76]:
morph_data = lemmatizer(data)

In [77]:
def extract_lemma(texts):
    norm = []
    for t in texts:
        res = []
        for word in t:
            n = word.normal_form
            res.append(n)
        norm.append(res)
    return norm

In [78]:
# This is our lemmatized data ready to be used further
normalized = extract_lemma(morph_data)

In [81]:
# Save json to load next time to avoid running again
with open('C:/Users/genya/Topic modelling/normalized.json', 'w') as fp:
    json.dump(normalized, fp)

In [82]:
# Opening json
with open('C:/Users/genya/Topic modelling/normalized.json') as f:
    data_norm = json.load(f)

In [157]:
# lemma with mystem - another russian lemmatizer (not used here): 
#def preprocess(text):
    #m = Mystem()
    #tokens = (t.lower() for t in m.lemmatize(text) if t.isalpha() and t.lower() not in stopwordsrus)
    #return list(tokens)

In [83]:
# Let's build the bigram and trigram models using gensim
bigram = gensim.models.Phrases(data_norm, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[data_norm], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)



In [84]:
def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

data_words_trigrams = make_trigrams(data_norm)

In [85]:
# We can see that bigrams and trigrams are build successfully 
print(data_words_trigrams[0])

['стать_известно', 'агентство', 'ассошиэйтед', 'пресс', 'экипаж', 'последний', 'экспедиция', 'станция', 'считать', 'способный', 'виктор', 'афанасьев', 'чувствовать', 'грустить', 'оставить', 'станция', 'летать', 'беспилотный', 'режим', 'gazeta', 'ru', 'подробно', 'писать', 'финансирование', 'программа', 'закрытый', 'конструктор', 'спешить', 'топить', 'тихий_океан', 'надеяться', 'изыскание', 'внебюджетный', 'надеяться', 'правительство', 'оплатить', 'финальный', 'экспедиция', 'февраль', 'март', 'новый', 'экспедиция', 'должный', 'постепенно', 'перевести', 'станция', 'низкий', 'орбита', 'тонный', 'основное', 'сгореть', 'атмосфера', 'незначительный', 'часть', 'упасть', 'тихий_океан', 'гарантия', 'пережить', 'столько', 'отказ', 'оборудование', 'конструкция', 'повести', 'адекватно', 'команда', 'афанасьев', 'перечислить', 'потенциально_опасный', 'элемент', 'конференция', 'состояться', 'понедельник', 'звёздный_городок', 'упасть', 'давление', 'кабина', 'стать', 'серьёзный', 'препятствие', 'работа

In [86]:
# Let's create dictionary of all our unique words from the dataset using corpora from gensim
dictionary = corpora.Dictionary(data_words_trigrams)
# Now let's create corpus where we count occurances for each word from dictionary in texts
corpus = [dictionary.doc2bow(doc) for doc in data_words_trigrams]
# We will also try to filter unimportant words by their tf-idf score, so let's create the tf-idf scores here too
tfidf = gensim.models.TfidfModel(corpus, id2word = dictionary)


In [87]:
dictionary[0]

'gazeta'

In [242]:
# We can have a look at "term-frequency" (occurance of each word) for each doc:
#[[(dictionary[id], freq) for id, freq in cp] for cp in corpus[:5]]

In [89]:
# Let's see what are the max and min values of tf-idf score:
tf_max = round(max([max([value for id, value in tfidf[corpus[x]]]) for x in range(len(corpus))]), 4)
tf_min = round(min([min([value for id, value in tfidf[corpus[x]]]) for x in range(len(corpus))]), 4)
print(tf_max, tf_min)
tfidf_range = [round(num, 3) for num in np.arange(tf_min, tf_max, 0.005).tolist()]
# We will be cutting the highest and the lowest tf-idf, e.g. <10 and >95% of all tf-idf values
print(np.percentile(tfidf_range, 95), np.percentile(tfidf_range, 10))


0.8703 0.004
0.82575 0.0905


In [90]:
#import itertools
#all_tfidfs = sorted(list(itertools.chain.from_iterable([[value for id, value in tfidf[corpus[x]]] for x in range(len(corpus))])))
#(extract all tf-idf to a list, not used here)

In [219]:
# Let's select high and low tfidf threshold values, and filter them out. 
# Thus, we will filter out very common (low tf-idf) and very rare (big tf-idf) words

low_value = np.percentile(tfidf_range, 5) #10
high_value = np.percentile(tfidf_range, 95) #86
#low_value = 0.12
#high_value = 0.7
filtered_corpus = []
for i in range(0, len(corpus)):
        
    filter_ids = [id for id, value in tfidf[corpus[i]] if value < low_value or value > high_value ]
   
    new_bow = [(index, value) for (index, value) in corpus[i] if index not in filter_ids] 

      
    filtered_corpus.append(new_bow)

In [243]:
# Our dictionary after filtering
#[[(dictionary[id], freq) for id, freq in cp] for cp in filtered_corpus[:10]]

In [27]:
# Now we have prepered the data. We have two types of corpus:
# original without tf-idf filtering called "corpus", and the one with tf-idf filtering called "filtered_corpus"

# Firtst, let's build LDA model from Gensim without tf-idf filtering.
# Since the number of texts is quite large (20000), let's chose number of topics equal to 150.
lda_model = gensim.models.ldamodel.LdaModel(corpus=corpus,
                                           id2word=dictionary,
                                           num_topics=100, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

In [28]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

[(36,
  '0.000*"низкообогащенный" + 0.000*"мессмера" + 0.000*"банкируруководитель" + '
  '0.000*"банкирвпервые" + 0.000*"ангель" + 0.000*"демобилизация" + '
  '0.000*"келиматовый" + 0.000*"сопасение" + 0.000*"будетлить" + '
  '0.000*"печень"'),
 (9,
  '0.000*"низкообогащенный" + 0.000*"мессмера" + 0.000*"банкируруководитель" + '
  '0.000*"банкирвпервые" + 0.000*"ангель" + 0.000*"демобилизация" + '
  '0.000*"келиматовый" + 0.000*"сопасение" + 0.000*"будетлить" + '
  '0.000*"печень"'),
 (60,
  '0.000*"низкообогащенный" + 0.000*"мессмера" + 0.000*"банкируруководитель" + '
  '0.000*"банкирвпервые" + 0.000*"ангель" + 0.000*"демобилизация" + '
  '0.000*"келиматовый" + 0.000*"сопасение" + 0.000*"будетлить" + '
  '0.000*"печень"'),
 (61,
  '0.283*"вновь" + 0.046*"сооружение" + 0.000*"низкообогащенный" + '
  '0.000*"банкируруководитель" + 0.000*"банкирвпервые" + 0.000*"ангель" + '
  '0.000*"демобилизация" + 0.000*"келиматовый" + 0.000*"сопасение" + '
  '0.000*"будетлить"'),
 (38,
  '0.135*"рези

In [29]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(corpus))  # a measure of how good the model is. The lower the better.



Perplexity:  -48.2338338769311


In [30]:
# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_words_trigrams, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  0.3702814239793627


In [33]:
# Now let's build basic Gensim LDA model with tf-idf filtering:
lda_model = gensim.models.ldamodel.LdaModel(corpus=filtered_corpus,
                                           id2word=dictionary,
                                           num_topics=100, 
                                           random_state=100,
                                           update_every=1,
                                           chunksize=100,
                                           passes=10,
                                           alpha='auto',
                                           per_word_topics=True)

In [34]:
# Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[filtered_corpus]

[(43,
  '0.000*"низкообогащенный" + 0.000*"мессмера" + 0.000*"банкируруководитель" + '
  '0.000*"банкирвпервые" + 0.000*"ангель" + 0.000*"демобилизация" + '
  '0.000*"келиматовый" + 0.000*"сопасение" + 0.000*"будетлить" + '
  '0.000*"печень"'),
 (88,
  '0.000*"низкообогащенный" + 0.000*"мессмера" + 0.000*"банкируруководитель" + '
  '0.000*"банкирвпервые" + 0.000*"ангель" + 0.000*"демобилизация" + '
  '0.000*"келиматовый" + 0.000*"сопасение" + 0.000*"будетлить" + '
  '0.000*"печень"'),
 (36,
  '0.000*"низкообогащенный" + 0.000*"мессмера" + 0.000*"банкируруководитель" + '
  '0.000*"банкирвпервые" + 0.000*"ангель" + 0.000*"демобилизация" + '
  '0.000*"келиматовый" + 0.000*"сопасение" + 0.000*"будетлить" + '
  '0.000*"печень"'),
 (61,
  '0.260*"вновь" + 0.000*"низкообогащенный" + 0.000*"мессмера" + '
  '0.000*"банкируруководитель" + 0.000*"банкирвпервые" + 0.000*"ангель" + '
  '0.000*"демобилизация" + 0.000*"келиматовый" + 0.000*"сопасение" + '
  '0.000*"будетлить"'),
 (38,
  '0.185*"инфор

In [35]:
# Compute Perplexity
print('\nPerplexity: ', lda_model.log_perplexity(filtered_corpus))  # a measure of how good the model is. lower the better.



Perplexity:  -57.02259091559352


In [36]:
# Compute Coherence Score
coherence_model_lda = CoherenceModel(model=lda_model, texts=data_words_trigrams, dictionary=dictionary, coherence='c_v')
coherence_lda = coherence_model_lda.get_coherence()
print('\nCoherence Score: ', coherence_lda)


Coherence Score:  0.33075086047076946


# Mallet LDA Model

In [122]:
# Now, let's builed Mallet LDA Model, first with unfiltered corpus:
import os
os.environ.update({'MALLET_HOME': r'C:/mallet/mallet-2.0.8/'})
mallet_path = r'C:/mallet/mallet-2.0.8/bin/mallet'
ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=corpus, num_topics=145, id2word=dictionary, random_seed=0)#150

In [123]:
# Show Topics
pprint(ldamallet.show_topics(formatted=False))

# Compute Coherence Score
coherence_model_ldamallet = CoherenceModel(model=ldamallet, texts=data_words_trigrams, dictionary=dictionary, coherence='c_v')
coherence_ldamallet = coherence_model_ldamallet.get_coherence()
print('\nCoherence Score: ', coherence_ldamallet)

[(108,
  [('оказаться', 0.03297125829087763),
   ('вызвать', 0.025377295011054502),
   ('прийтись', 0.022878015956935498),
   ('некоторый', 0.019801980198019802),
   ('заметить', 0.019032971258290877),
   ('который', 0.019032971258290877),
   ('ошибка', 0.018840719023358647),
   ('сообщение', 0.017591079496299143),
   ('решить', 0.016437566086705758),
   ('возникнуть', 0.01489954820724791)]),
 (128,
  [('россия', 0.0813588850174216),
   ('мвф', 0.03231707317073171),
   ('банка', 0.030226480836236934),
   ('кредит', 0.028658536585365855),
   ('банк', 0.025609756097560974),
   ('доллар', 0.022735191637630662),
   ('центробанк', 0.022125435540069686),
   ('финансовый', 0.02029616724738676),
   ('российский', 0.019686411149825785),
   ('центральный', 0.0195993031358885)]),
 (72,
  [('бюджет', 0.07618753855644664),
   ('правительство', 0.06153608883405305),
   ('средство', 0.04287476866132017),
   ('федеральный', 0.04094694632942628),
   ('финансирование', 0.027683528685996297),
   ('миллиа

In [124]:
model_topics = ldamallet.show_topics(formatted=False)
pprint(ldamallet.print_topics(num_words=10))

[(3,
  '0.076*"мнение" + 0.065*"считать" + 0.036*"такой" + 0.028*"подобный" + '
  '0.022*"полагать" + 0.018*"случай" + 0.017*"мочь" + 0.015*"привести" + '
  '0.015*"поскольку" + 0.014*"необходимый"'),
 (43,
  '0.031*"пользователь" + 0.029*"программа" + 0.023*"вирус" + 0.018*"письмо" + '
  '0.017*"компания" + 0.014*"компьютер" + 0.013*"файл" + 0.013*"дать" + '
  '0.012*"адрес" + 0.010*"почтовый"'),
 (57,
  '0.049*"женщина" + 0.026*"жена" + 0.022*"девушка" + 0.019*"друг" + '
  '0.018*"муж" + 0.014*"молодая" + 0.013*"мужчина" + 0.013*"один" + '
  '0.011*"семья" + 0.011*"рассказать"'),
 (60,
  '0.050*"получить" + 0.031*"хороший" + 0.027*"конкурс" + 0.025*"премия" + '
  '0.022*"награда" + 0.018*"приз" + 0.018*"вручить" + 0.014*"стать" + '
  '0.013*"среди" + 0.011*"назвать"'),
 (90,
  '0.081*"число" + 0.057*"тысяча" + 0.053*"количество" + 0.045*"данные" + '
  '0.041*"миллион" + 0.030*"составлять" + 0.027*"общий" + 0.024*"сообщать" + '
  '0.022*"примерно" + 0.019*"настоящее"'),
 (31,
  '0.070

In [244]:
def format_topics_sentences(ldamodel, corpus, texts):
    # Init output
    sent_topics_df = pd.DataFrame (index=range(20000), columns = ['Dominant_Topic1', 'Dominant_Topic2', '%Topic_Contribution1', '%Topic_Contribution2', 'Topic_Keywords1', 'Topic_Keywords2'])
    #sent_topics_df = pd.DataFrame()
    

    # Get main topic in each document
    for i, text in enumerate(ldamodel[corpus]):
        text = sorted(text, key=lambda x: (x[1]), reverse=True) #sort % contributions of topic  
        # Get the Dominant topic, % of topic contribution and Keywords for each document
        for j, (topic_num, topic_contrib) in enumerate(text):
            if j == 0:  # => dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = ", ".join([word for word, prop in wp])
                sent_topics_df.Dominant_Topic1[i] = int(topic_num)
                sent_topics_df['%Topic_Contribution1'][i] = round(topic_contrib,4)
                sent_topics_df['Topic_Keywords1'][i] = topic_keywords
                
                #sent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
                
            elif j == 1:  # => second dominant topic
                wp = ldamodel.show_topic(topic_num)
                topic_keywords = ", ".join([word for word, prop in wp])
                sent_topics_df.Dominant_Topic2[i] = int(topic_num)
                sent_topics_df['%Topic_Contribution2'][i] = round(topic_contrib,4)
                sent_topics_df['Topic_Keywords2'][i] = topic_keywords
                #ent_topics_df = sent_topics_df.append(pd.Series([int(topic_num), round(prop_topic,4), topic_keywords]), ignore_index=True)
            else:
                break
    #sent_topics_df.columns = ['First Dominant_Topic', 'Second dominant topic', 'Perc_Contribution', 'Topic_Keywords']

    # Add original text to the end of the output
    contents = pd.Series(texts)
    sent_topics_df = pd.concat([sent_topics_df, contents], axis=1)
    return(sent_topics_df)


df_topic_sents_keywords = format_topics_sentences(ldamodel=ldamallet, corpus=corpus, texts=rusdata[:20000])

# Format
df_dominant_topic = df_topic_sents_keywords.reset_index(drop = True)
#df_dominant_topic.columns = ['Document_No', 'First Dominant_Topic', 'Second dominant topic', 'Topic_Perc_Contrib', 'Keywords', 'Text']

# Show
df_dominant_topic.head(10)

Dominant_Topic1 Dominant_Topic2 %Topic_Contribution1 %Topic_Contribution2  \
0              96              31               0.2314               0.0497   
1             111              92               0.2062                0.079   
2              46              70               0.1393               0.0781   
3               8              49               0.1926               0.0428   
4              63             121               0.1988               0.0454   
5               7              20               0.0848               0.0559   
6              55             139               0.0933               0.0813   
7              23              81                0.249               0.0345   
8             126             129               0.2858                0.039   
9              69              92               0.1401               0.0193   

                                     Topic_Keywords1  \
0  станция, спутник, казахстан, запуск, космическ...   
1  взрыв, теракт, произойти, результат, погибнуть...   
2  бюджет, средство, долг, сумма, миллиард_рубль,...   
3  британский, великобритания, лондон, английский...   
4  российский, мвф, фонд, сторона, пиночет, между...   
5  продукция, рынок, тонна, товар, таможенный, то...   
6  государственный, соответствие, федеральный, ро...   
7  врач, больница, состояние, медицинский, заболе...   
8  партия, движение, лидер, организация, политиче...   
9  район, вода, землетрясение, дом, пострадавший,...   

                                     Topic_Keywords2  \
0  система, проблема, эксперт, серьёзный, специал...   
1  находиться, человек, число, среди, данные, тыс...   
2  представитель, официальный, япония, японский, ...   
3  заявление, говориться, письмо, обратиться, про...   
4  провести, операция, проведение, ход, мероприят...   
5  проверка, деятельность, налог, налоговый, пред...   
6  управление, мвд, фсб, сотрудник, внутренний, о...   
7  решение, принять, суд, верховный_суд, судья, р...   
8  область, владимир, александр, губернатор, моск...   
9  находиться, человек, число, среди, данные, тыс...   

                                                text  
0  Как стало известно агентству Ассошиэйтед Пресс...  
1  В зале игровых автоматов в третьем ярусе подзе...  
2  Япония приняла решение разморозить кредиты Рос...  
3  Британцы отмечают сегодня скорбную дату - втор...  
4  В понедельник директор департамента внешних св...  
5  С 1 сентября на всей территории России вводитс...  
6  Указом президента России Бориса Ельцина внесен...  
7  Сегодня областной центр Сахалина и Курил получ...  
8  Бывший шеф Службы безопасности президента  Але...  
9  подземный толчок силой 5,2 балла На северо-зап...

In [235]:
# Here we can select a text and see its first and second most dominant topics (keywords of those topics)
index = 3
df_dominant_topic['text'][index]

'Британцы отмечают сегодня скорбную дату - вторуюгодовщину со дня смерти принцессы Дианы. Она погибла вавтомобильной катастрофе в парижском туннеле в ранние утренниечасы 31 августа 1997 года. С утра к золоченым воротамКенсингтонского дворца, где жила Диана, приходят ее поклонники.В чугунные завитки ограды вплетаются сотни букетов. Людиоставляют дары принцессе - коробки конфет, плюшевых мишек,открытки со посвященными ей стихами, стенгазеты. Вчера и сегодня болееТысячи англичан подписали петицию с требованием к властямускорить сооружение мемориала принцессе. Пока Мемориальныйкомитет собирается переоборудовать в ее честь детскую игровуюплощадку, которая находится на территории Кенсингтонского паркаи создать посвященную ей "прогулочную дорожку" вдоль похоронного маршрута. Мемориальный фонд имени принцессы Дианы собрал в видепожертвований населения более 85 миллонов фунтов (140 миллионов долларов).Средичленов правления фонда нет согласия относительно использованиясредств. Они заняты не стол

In [236]:
df_dominant_topic['Topic_Keywords1'][index]+'// '+df_dominant_topic['Topic_Keywords2'][index]

'британский, великобритания, лондон, английский, англия, ввс, армения, bbc, лондонский, фунт// погибший, тело, смерть, семья, родственник, останки, гибель, имя, экспертиза, кладбище'

# LDA Mallet with high and low tf-idf filtered out

In [221]:
# Now let's build Mallet LDA with tf-idf -filtered corpus:
import os
os.environ.update({'MALLET_HOME': r'C:/mallet/mallet-2.0.8/'})
mallet_path = r'C:/mallet/mallet-2.0.8/bin/mallet'
ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=filtered_corpus, num_topics=145, id2word=dictionary, random_seed=0)#150

In [222]:
# Show Topics
pprint(ldamallet.show_topics(formatted=False))

# Compute Coherence Score
coherence_model_ldamallet = CoherenceModel(model=ldamallet, texts=data_words_trigrams, dictionary=dictionary, coherence='c_v')
coherence_ldamallet = coherence_model_ldamallet.get_coherence()
print('\nCoherence Score: ', coherence_ldamallet)

[(63,
  [('российский', 0.4637861010830325),
   ('мвф', 0.04162906137184116),
   ('фонд', 0.023465703971119134),
   ('сторона', 0.016245487364620937),
   ('пиночет', 0.014778880866425993),
   ('международный', 0.014327617328519856),
   ('чили', 0.011845667870036101),
   ('международный_валютный_фонд', 0.01049187725631769),
   ('миссия', 0.009589350180505414),
   ('всемирный_банка', 0.007220216606498195)]),
 (80,
  [('тюрьма', 0.04748603351955307),
   ('турция', 0.04120111731843575),
   ('заключённый', 0.034217877094972066),
   ('латвия', 0.030726256983240222),
   ('турецкий', 0.022905027932960894),
   ('камера', 0.019553072625698324),
   ('содержаться', 0.015083798882681564),
   ('латвийский', 0.01494413407821229),
   ('освобождение', 0.013128491620111732),
   ('совершить', 0.012569832402234637)]),
 (109,
  [('сайт', 0.11266452547389634),
   ('интернет', 0.062283519113294286),
   ('пользователь', 0.02846526859374016),
   ('сервер', 0.01788525725801373),
   ('сеть', 0.014547515586623842

In [223]:
model_topics = ldamallet.show_topics(formatted=False)
pprint(ldamallet.print_topics(num_words=10))

[(13,
  '0.327*"президент" + 0.084*"путин" + 0.073*"владимир_путин" + '
  '0.065*"государство" + 0.029*"глава" + 0.027*"белоруссия" + '
  '0.022*"борис_ельцин" + 0.020*"кремль" + 0.014*"белорусский" + '
  '0.012*"ельцин"'),
 (2,
  '0.150*"информация" + 0.080*"дать" + 0.068*"сообщение" + 0.062*"агентство" + '
  '0.030*"источник" + 0.030*"сведение" + 0.027*"подтвердить" + 0.019*"никакой" '
  '+ 0.019*"появиться" + 0.018*"поступать"'),
 (7,
  '0.030*"продукция" + 0.027*"рынок" + 0.023*"тонна" + 0.021*"товар" + '
  '0.016*"таможенный" + 0.016*"торговля" + 0.015*"производство" + '
  '0.014*"производитель" + 0.013*"водка" + 0.012*"поставка"'),
 (122,
  '0.030*"курск" + 0.017*"подлодка" + 0.016*"норвежский" + 0.016*"водолаз" + '
  '0.014*"подводный_лодка" + 0.012*"операция" + 0.011*"лодка" + 0.011*"моряк" '
  '+ 0.010*"столкновение" + 0.010*"поднять"'),
 (131,
  '0.301*"рф" + 0.117*"республика" + 0.058*"март" + 0.049*"рбк" + '
  '0.021*"республиканский" + 0.020*"татарстан" + 0.014*"башкирия" 

In [224]:
df_topic_sents_keywords = format_topics_sentences(ldamodel=ldamallet, corpus=filtered_corpus, texts=rusdata[:20000])

df_dominant_topic_filtered_idfs = df_topic_sents_keywords.reset_index(drop = True)

# Show
df_dominant_topic_filtered_idfs.head(10)

Dominant_Topic1 Dominant_Topic2 %Topic_Contribution1 %Topic_Contribution2  \
0              96              31               0.2292                0.061   
1             111              92               0.2136               0.0885   
2              46              70               0.1589               0.0862   
3               8              87               0.2738               0.0472   
4              63             121               0.2561                0.047   
5               7              20                0.097               0.0719   
6              55             139               0.1094               0.0863   
7              23              81               0.2671               0.0365   
8             126             129               0.3082               0.0464   
9              69              92               0.1446               0.0224   

                                     Topic_Keywords1  \
0  станция, спутник, казахстан, запуск, космическ...   
1  взрыв, теракт, произойти, результат, погибнуть...   
2  бюджет, средство, долг, сумма, миллиард_рубль,...   
3  британский, великобритания, лондон, английский...   
4  российский, мвф, фонд, сторона, пиночет, между...   
5  продукция, рынок, тонна, товар, таможенный, то...   
6  государственный, соответствие, федеральный, ро...   
7  врач, больница, состояние, медицинский, заболе...   
8  партия, движение, лидер, организация, политиче...   
9  район, вода, землетрясение, дом, пострадавший,...   

                                     Topic_Keywords2  \
0  система, проблема, эксперт, серьёзный, специал...   
1  находиться, человек, число, среди, данные, тыс...   
2  представитель, официальный, япония, японский, ...   
3  женщина, жена, дочь, семья, муж, мужчина, сын,...   
4  провести, операция, проведение, ход, мероприят...   
5  проверка, деятельность, налог, налоговый, пред...   
6  управление, мвд, фсб, сотрудник, внутренний, о...   
7  решение, принять, суд, верховный_суд, судья, р...   
8  область, владимир, александр, губернатор, моск...   
9  находиться, человек, число, среди, данные, тыс...   

                                                text  
0  Как стало известно агентству Ассошиэйтед Пресс...  
1  В зале игровых автоматов в третьем ярусе подзе...  
2  Япония приняла решение разморозить кредиты Рос...  
3  Британцы отмечают сегодня скорбную дату - втор...  
4  В понедельник директор департамента внешних св...  
5  С 1 сентября на всей территории России вводитс...  
6  Указом президента России Бориса Ельцина внесен...  
7  Сегодня областной центр Сахалина и Курил получ...  
8  Бывший шеф Службы безопасности президента  Але...  
9  подземный толчок силой 5,2 балла На северо-зап...

In [231]:
# To see an example of how the model worked: we can pick a text by index, and see the keywords of most dominant topic
# (with higest contribution, as well as the second one)
index = 13
df_dominant_topic_filtered_idfs['text'][index]

'15 представителей национал-большевистской партии России, разбрасывавших в День независимости Украины 24 августа в Севастополе листовки антиукраинского содержания, могут получить наказание по суду до 5 лет лишения свободы. Как сообщает "Интерфакс-Украина", действия "лимоновцев", забравшихся 24 августа на башню часов Севастопольского патриотического клуба Черноморского  флота РФ и с выкриками "Севастополь! Крым! Россия!" разбрасывавших оттуда листовки, квалифицированы правоохранительными органами Украины как злостное хулиганство. Против  активистов   партии  Эдуарда   Лимонова   возбуждено уголовное дело,  предусматривающее наказание на срок от одного до пяти лет лишения свободы. В  ходе следственных  мероприятий  милиция установила причастность  к группе ряда местных жителей - в результате проведенных обысков у них были изъяты программные документы национал-большевистской партии России, а также переписка членов партии с  лидером Эдуардом Лимоновым.  Изъяты также  листовки  и  газеты на

In [232]:
# Two most dominint topics (their keywords)
df_dominant_topic_filtered_idfs['Topic_Keywords1'][index]+'// '+df_dominant_topic_filtered_idfs['Topic_Keywords2'][index]

'украина, украинский, киев, чехия, болгария, чешский, кучма, крым, болгарский, иван// партия, движение, лидер, организация, политический, объединение, союз, съезд, блок, единство'

In [ ]:
# By reviewing several texts and their first and second most dominant topics, it appears that model with unfiltered corpus 
# gives more consistent results.  

# Now let's plot 20 most frequent topics from our 20000 texts, as well as the second most frequent topic
# Let's organize data for the plot

In [188]:
# Counting texts for each topic number
counts = []
n_topics = 145
for x in range(0, n_topics):
    z = df_dominant_topic['Dominant_Topic1'][df_dominant_topic['Dominant_Topic1'] == x].count()
    counts.append([x,z])

In [189]:
# Sorting by number of texts
sorted_counts = sorted(counts, key=lambda x: int(x[1]), reverse=True) 


In [190]:
# Selecting most popular n-themes
n_themes = 25
most_popular = [sorted_counts[x][0] for x in range(n_themes)] 


In [191]:
# Selecting keywords for most popular n-themes
theme_keywords = [df_dominant_topic['Topic_Keywords1'][df_dominant_topic['Dominant_Topic1']==x].unique().tolist() for x in most_popular]

In [192]:
# Count number of texts for second topics
topic_counts = []
n_topics = 150
for x in range(0, n_topics):
    for y in range(0, n_topics):
        z = df_dominant_topic['Dominant_Topic1'][(df_dominant_topic['Dominant_Topic1'] == x) & (df_dominant_topic['Dominant_Topic2'] == y)].count()
        topic_counts.append([x,y,z])

In [193]:
# Sorting 
two_themes_count = sorted(topic_counts, key=lambda x: int(x[2]), reverse=True) 


In [194]:
# Selecting second topics for first popular n-topics
most_frequent = [two_themes_count[ind] for ind in range(len(two_themes_count)) if two_themes_count[ind][0] in most_popular]

In [195]:
most_frequent_sorted = sorted(most_frequent, key=lambda x: int(x[0]), reverse=True) 

In [196]:
# Selecting most frequent second topics that follow those most frequent first topics
second_topic = []
for x in most_popular:
    for y in range(len(most_frequent_sorted)):
        if most_frequent_sorted[y][0] == x:
            second_topic.append(most_frequent_sorted[y:y+1][0])
            break

In [197]:
# Getting array of second topic numbers
second_topic_num = [second_topic[x][1] for x in range(n_themes)]

In [198]:
# Corresponding keywords for second topics
theme_keywords_second_topic = [df_dominant_topic['Topic_Keywords2'][df_dominant_topic['Dominant_Topic2']==x].unique().tolist() for x in second_topic_num]

In [199]:
theme_keywords_second_topic

[['военнослужащий, чечня, район, боевик, мвд, раненый, милиционер, сотрудник, грозный, погибнуть'],
 ['хотеть, друг, девушка, думать, узнать, знать, прийти, рассказать, счастливый, любовь'],
 ['встреча, вопрос, проблема, переговоры, ход, глава, обсуждаться, министр_иностранный, обсудить, состояться'],
 ['третье, команда, занять, очки, победа, место, два, цска, занимать, тур'],
 ['погибший, тело, смерть, семья, родственник, останки, гибель, имя, экспертиза, кладбище'],
 ['боевик, район, чечня, федеральный_сила, грозный, военный, населить_пункт, уничтожить, федеральный_войско, отряд'],
 ['произойти, результат, погибнуть, пострадавший, пострадать, находиться, двое, получить, госпитализировать, авария'],
 ['боевик, район, чечня, федеральный_сила, грозный, военный, населить_пункт, уничтожить, федеральный_войско, отряд'],
 ['область, губернатор, регион, московский, областной, округа, подмосковье, владимир, региональный, администрация'],
 ['произойти, результат, погибнуть, пострадавший, постр

In [200]:
rcParams['font.size'] = 8
rcParams['axes.titlesize'] = 14
plt.rc('xtick', labelsize=14)
plt.rc('ytick', labelsize=14)
plt.rc('axes', labelsize=14)
rcParams['figure.dpi']= 600

theme = [sorted_counts[x][0] for x in range(n_themes)]
text_count = [sorted_counts[x][1] for x in range(n_themes)]
y_pos = np.arange(len(theme))
#fig = plt.figure(figsize=(5, 5))

# We will plot from the dataframe
# Graph 1
#x = fig.add_subplot(121)
fig, ax = plt.subplots(figsize=(16, 14))

plot = ax.barh(y_pos, text_count, align='center')
ax.set_yticks(y_pos)
ax.set_yticklabels(theme)
ax.invert_yaxis()  # labels read top-to-bottom
ax.set_xlabel('N of texts')
ax.set_ylabel('Topic number')
ax.set_title('25 most frequent topics')

x_offset = -200
y_offset = 0.3

for ind, bar in enumerate(plot):
    
    yloc = bar.get_y() + bar.get_height() / 2
    width = int(bar.get_width())
    ax.annotate('T1: '+', '.join(theme_keywords[ind][0].split(', ')[:4])+'\n'+', '.join(theme_keywords[ind][0].split(', ')[5:10]), xy=(width+x_offset, yloc+y_offset), fontsize=10)



#for ind, p in enumerate(ax.patches):
   # b = p.get_bbox()
    #val = "{:.0f}".format(b.x1)        
    #ax.annotate('T1: '+', '.join(theme_keywords[ind][0].split(', ')[:4])+'\n'+', '.join(theme_keywords[ind][0].split(', ')[5:10]), (5, b.y1 + y_offset), fontsize=4)
    

x_offset = 20
y_offset = 0.3
for ind, bar in enumerate(plot):
    #b = p.get_bbox()
    
    #val = "{:.0f}".format(b.x1) 
    yloc = bar.get_y() + bar.get_height() / 2
    width = int(bar.get_width())
    #ax.annotate('T2: '+', '.join(theme_keywords_second_topic[ind][0].split(', ')[:4])+'\n'+', '.join(theme_keywords_second_topic[ind][0].split(', ')[5:10]), (500, b.y1 + y_offset), fontsize=4)
    ax.annotate('T2: '+', '.join(theme_keywords_second_topic[ind][0].split(', ')[:4])+'\n'+', '.join(theme_keywords_second_topic[ind][0].split(', ')[5:10]), xy=(width+x_offset, yloc+y_offset), fontsize=10)



plt.show()

- Each document can be described by a distribution of topics [T1 + T2 + T3 + ... + T150] and each topic can be described by a distribution of words, where T1 - topic with highest contribution, thus T1 considered as the prevalent topic of text.
<br>
- Hovewer it makes sence to look at the second or even third topic in order to get broader overview and better idea of what the text is about.
<br>
- In the graph, the most frequent topics (T1) are represented, as well as most frequent T2, following that T1. 